In [122]:
import copy
import csv
import functools
import glob
import os

In [123]:
from collections import namedtuple

In [124]:
import SimpleITK as sitk # 데이터 파일 포맷을 numpy로 불러들이기 위함
import numpy as np

In [125]:
import torch
import torch.cuda
from torch.utils.data import Dataset

In [126]:
import os
os.getcwd()

'D:\\Lung_Cancer_Diagnostic\\LunaDataset'

In [176]:
from util.disk import getCache # diskcache disk에  cache를 저장해주는 라이브러리
from util.util import XyzTuple, xyz2irc
from util.logconf import logging

In [177]:
log = logging.getLogger(__name__)
log.setLevel(logging.DEBUG)

In [178]:
raw_cache = getCache('part2ch10_raw')

In [179]:
CandidateInfoTuple = namedtuple(
    'CandidateInfoTuple',
    'isNodule_bool, diameter_mm, series_uid, center_xyz',
)

In [195]:
"""
- 인메모리나 온디스크 캐싱을 적절하게 사용하여 데이터 파이프라인 속도를 올려 놓으면 훈련 속도가 상당히 개선됨
- 훈련 데이터셋 전체를 사용하게 되면 다운로드도 오래 걸리고 필요한 디스크 공간도 커지기 때문에 전체를 사용하는 대신 훈련 프로그램 실행에 집중
- requireOnDisk_bool 파라미터를 사용하여 디스크 상에서 시리즈 UID가 발견되는 LUNA 데이터만 사용하고 이에 해당하는 엔트리는 csv에서 거름
"""

@functools.lru_cache(1000) # 표준 인메모리 캐싱 라이브러리
def getCandidateInfoList(requireOnDisk_bool=True): # disk에 없는 데이터를 거르기 위함
    # 모든 디스크에 있는 모든 세트를 series_uids로 구성함
    # 이렇게 하면 모든 하위 집합을 다운로드 하지 않더라도 사용할 수 있음
    mhd_list = glob.glob('D:/Luna/subset*/*.mhd')
    presentOnDisk_set = {os.path.split(p)[-1][:-4] for p in mhd_list}
    
    diameter_dict = {}
    with open("D:/Luna/annotations.csv", "r") as f:
        for row in list(csv.reader(f))[1:]:
            series_uid = row[0] # user_id
            annotationCenter_xyz = tuple([float(x) for x in row[1:4]]) # xyz 좌표
            annotationDiameter_mm = float(row[4]) # 차원 정보
            
            diameter_dict.setdefault(series_uid, []).append( # 첫번째 인자로 키값, 두번째 인자로 기본값을 넘김
                (annotationCenter_xyz, annotationDiameter_mm)
            )
    
    candidateInfo_list = []
    with open('D:/Luna/candidates.csv', "r") as f:
        for row in list(csv.reader(f))[1:]:
            series_uid = row[0] # user_id
            
            if series_uid not in presentOnDisk_set and requireOndisk_bool: # series_uid가 없으면 서브셋에 있지만 디스크에는 없으므로 건너뜀
                continue
                
            isNodule_bool = bool(int(row[4])) # 클래스
            candidateCenter_xyz = tuple([float(x) for x in row[1:4]]) # xyz 좌표
            
            candidateDiameter_mm = 0.0
            for annotation_tup in diameter_dict.get(series_uid, []):
                annotation_xyz, annotationDiameter_mm = annotation_tup
                for i in range(3):
                    delta_mm = abs(candidateCenter_xyz[i] - annotationCenter_xyz[i])
                    if delta_mm > annotationDiameter_mm / 4: # 반경을 얻기 위해 직경을 2로 나누고, 두 개의 결절 센터가 결절의 크기 기준으로
                        break                                # 너무 떨어져 있는 지를 반지름의 절반 길이를 기준으로 판정한다.(바운딩 박스 체크)
                else:
                    candidateDiameter_mm = annotationDiameter_mm
                    break
                    
            candidateInfo_list.append(CandidateInfoTuple(
                isNodule_bool,
                candidateDiameter_mm,
                series_uid,
                candidateCenter_xyz,
            ))
            
    candidateInfo_list.sort(reverse=True) # s내림차순 정렬
    return candidateInfo_list

In [276]:
# @functools.lru_cache(1, typed=True)
def getCt(series_uid):
    return Ct(series_uid)

In [277]:
@raw_cache.memoize(typed=True)
def getCtRawCandidate(series_uid, center_xyz, width_irc):
    ct = getCt(series_uid)
    ct_chunk, center_irc = ct.getRawCandidate(center_xyz, width_irc)
    return ct_chunk, center_irc

# 개별 CT 스캔 로딩
- 디스크에서 CT 데이터를 얻어와 파이썬 객체로 변환 후 3차원 결절 밀도 데이터로 사용할 수 있도록 만드는 작업
- CT 스캔 파일의 원래 포맷은 DICOM이라고 부름
- CT 스캔 복셀은 하운스필드 단위(https://en.wikipedia.org/wiki/Hounsfield_scale) 로 표시

In [278]:
class Ct:
    def __init__(self, series_uid):
        mhd_path = glob.glob(
            'D:/Luna/subset*/{}.mhd'.format(series_uid)
        )[0]
        
        ct_mhd = sitk.ReadImage(mhd_path) # sitk.ReadImage는 .mhd 파일뿐 아니라 .raw 파일도 읽음
        ct_a = np.array(sitk.GetArrayFromImage(ct_mhd), dtype=np.float32)
        
        """
        공기는 -1000HU(0g/cc), 물은 0HU(1g/cc), 뼈는 +1000HU(2~3g/cc)다. 
        우리가 관심잇는 종양은 대체로 1g/cc(0HU) 근처이므로 -1000HU, 1000HU을 제거하고 1g/cc가 아닌 것도 제거함
        """ 
        ct_a.clip(-1000, 1000, ct_a)
        
        self.series_uid = series_uid
        self.hu_a = ct_a
        
        """
        환자 좌표계를 사용해 결절 위치 정하기
        util.py에 있음
        1. 좌표를 XYZ 체계로 만들기 위해 IRC에서 CRI로 뒤집음
        2. 인덱스를 복셀 크기로 확대 축소
        3. 파이썬의 @를 사용하여 방향을 나타내는 행렬과 행렬곱을 수행
        4. 기준으로부터 오프셋을 더함
        """
        self.origin_xyz = XyzTuple(*ct_mhd.GetOrigin())
        self.vxSize_xyz = XyzTuple(*ct_mhd.GetSpacing())
        self.direction_a = np.array(ct_mhd.GetDirection()).reshape(3, 3) # 방향 정보를 배열로 변환하고 3 x 3 행렬 모양의 9개 요소의 배열을 reshape함
    
    # 큰 CT 복셀 배열에서 후보의 중심 배열 좌표 정보(인덱스, 행, 열)을 사용하여 후보 샘플을 잘라내기
    def getRawCandidate(self, center_xyz, width_irc):
        center_irc = xyz2irc(
            center_xyz,
            self.origin_xyz,
            self.vxSize_xyz,
            self.direction_a,
        )
        
        slice_list = []
        for axis, center_val in enumerate(center_irc):
            start_ndx = int(round(center_val - width_irc[axis]/2))
            end_ndx = int(start_ndx + width_irc[axis])
            slice_list.append(slice(start_ndx, end_ndx))
            
        ct_chunk = self.hu_a[tuple(slice_list)]
        
        return ct_chunk, center_irc
        

# 간단한 데이터셋 구현
- Luna 데이터셋 구현
- 초기화 후에 하나의 상수값을 반환하는 __len__ 구현
- 인덱스를 인자로 받아 훈련(경우에 따라서는 검증)에서 사용할 샘플 데이터 튜플을 반환하는 __getitem__ 메소드
- __len__이 N값을 반환한다면 __getitem__은 0에서 N-1까지의 입력값에 대한 유효값을 넘겨줘야함

In [279]:
class LunaDataset(Dataset):
    def __init__(self,
                val_stride=0,
                isValSet_bool=None,
                series_uid=None,
                randomize=False,
                ):
        
        copy_candidateInfo_list = copy.copy(getCandidateInfoList())
        
        if randomize==True:
            import random
            self.candidateInfo_list = random.sample(copy_candidateInfo_list, len(copy_candidateInfo_list))
        else:
            self.candidateInfo_list = copy_candidateInfo_list
    
        
        if series_uid:
            self.candidateInfo_list = [
                x for x in self.candidateInfo_list if x.series_uid == series_uid
            ]
            
        if isValSet_bool:
            assert val_stride > 0, val_stride
            self.candidateInfo_list = self.getCandidateInfoList[::val_stride]
            assert self.candidateInfo_list
        elif val_stride > 0:
            del self.candidateInfo_list[::val_stride]
            assert self.candidateInfo_list
        
        log.info("{!r}: {} {} samples".format(
            self,
            len(self.candidateInfo_list),
            "validation" if isValSet_bool else "training",
        ))
        
        
        
    def __len__(self):
        return len(self.candidateInfo_list)
    
    def __getitem__(self, ndx):
        candidateInfo_tup = self.candidateInfo_list[ndx]
        width_irc = (32, 48, 48)
        
        candidate_a, center_irc = getCtRawCandidate(
            candidateInfo_tup.series_uid,
            candidateInfo_tup.center_xyz,
            width_irc,
        )
        
        candidate_t = torch.from_numpy(candidate_a)
        candidate_t = candidate_t.to(torch.float32)
        candidate_t = candidate_t.unsqueeze(0) # .unsqueeze(0)으로 '채널' 차원 추가
        
        pos_t = torch.tensor([
                not candidateInfo_tup.isNodule_bool,
                candidateInfo_tup.isNodule_bool
            ],
            dtype=torch.long,
        )
        
        # 훈련 샘플 반환
        return (
                candidate_t,
                pos_t,
                candidateInfo_tup.series_uid,
                torch.tensor(center_irc),
        )

In [280]:
# 캐시 클리어 전
print(getCandidateInfoList.cache_info())

# 캐시 클리어 후
getCandidateInfoList.cache_clear()
print(getCandidateInfoList.cache_info())

CacheInfo(hits=5, misses=1, maxsize=1000, currsize=1)
CacheInfo(hits=0, misses=0, maxsize=1000, currsize=0)


In [281]:
# 처음 tensor는 candidate_t
# 두번째는 cls_t
# 세번째는 candidate_tup.series_uid
# 네번째는 center_irc
print(LunaDataset(randomize=True))

2022-09-02 16:55:24,684 INFO     pid:18408 __main__:031:__init__ <__main__.LunaDataset object at 0x000001E9E8F215B0>: 551065 training samples


In [270]:
print(LunaDataset()[0][0])

2022-09-02 16:31:45,368 INFO     pid:18408 __main__:031:__init__ <__main__.LunaDataset object at 0x000001E9E9A8E9D0>: 551065 training samples


tensor([[[[-563., -282.,  -95.,  ...,   33.,   48.,   46.],
          [-445., -195.,  -65.,  ...,   25.,   27.,   26.],
          [-447., -203.,  -59.,  ...,    4.,    8.,   13.],
          ...,
          [ -19., -121., -221.,  ...,   22.,   47.,   58.],
          [ -58., -182., -283.,  ...,   16.,   37.,   49.],
          [-142., -273., -380.,  ...,   25.,   41.,   44.]],

         [[-729., -569., -374.,  ...,   17.,   23.,   27.],
          [-650., -502., -316.,  ...,   20.,   10.,   18.],
          [-663., -483., -249.,  ...,    9.,   -1.,   16.],
          ...,
          [-119., -147., -205.,  ...,   25.,   50.,   69.],
          [ -98., -163., -229.,  ...,   14.,   27.,   47.],
          [-102., -203., -304.,  ...,   18.,   19.,   39.]],

         [[-866., -824., -718.,  ...,   -5.,   -7.,    1.],
          [-829., -792., -653.,  ...,    1.,   -6.,    1.],
          [-806., -736., -517.,  ...,   14.,    3.,    7.],
          ...,
          [-283., -293., -307.,  ...,   54.,   67.,

In [282]:
import time
# dataset = LunaDataset(randomize=True) 랜덤화 True
# random화 False
dataset = LunaDataset(randomize=False)

def lunadataset(dataset):
    luna_dataset = []
    count = 0
    start_time = time.time()
    for i in range(1000):
        print(dataset[i])
        count += 1
    end_time = time.time()
    print("걸린 시간은 {}초입니다.".format(end_time - start_time))
    print("count: {}".format(count))
    

2022-09-02 16:55:34,291 INFO     pid:18408 __main__:031:__init__ <__main__.LunaDataset object at 0x000001E9E8F215B0>: 551065 training samples


In [283]:
luna = lunadataset(dataset)

(tensor([[[[-563., -282.,  -95.,  ...,   33.,   48.,   46.],
          [-445., -195.,  -65.,  ...,   25.,   27.,   26.],
          [-447., -203.,  -59.,  ...,    4.,    8.,   13.],
          ...,
          [ -19., -121., -221.,  ...,   22.,   47.,   58.],
          [ -58., -182., -283.,  ...,   16.,   37.,   49.],
          [-142., -273., -380.,  ...,   25.,   41.,   44.]],

         [[-729., -569., -374.,  ...,   17.,   23.,   27.],
          [-650., -502., -316.,  ...,   20.,   10.,   18.],
          [-663., -483., -249.,  ...,    9.,   -1.,   16.],
          ...,
          [-119., -147., -205.,  ...,   25.,   50.,   69.],
          [ -98., -163., -229.,  ...,   14.,   27.,   47.],
          [-102., -203., -304.,  ...,   18.,   19.,   39.]],

         [[-866., -824., -718.,  ...,   -5.,   -7.,    1.],
          [-829., -792., -653.,  ...,    1.,   -6.,    1.],
          [-806., -736., -517.,  ...,   14.,    3.,    7.],
          ...,
          [-283., -293., -307.,  ...,   54.,   67.

(tensor([[[[ -930.,  -987.,  -974.,  ...,  -771.,  -803.,  -898.],
          [ -921.,  -929., -1000.,  ...,  -964.,  -912.,  -872.],
          [ -912.,  -969., -1000.,  ...,  -884.,  -877.,  -865.],
          ...,
          [ -866.,  -888.,  -944.,  ...,  -910.,  -972., -1000.],
          [ -739.,  -802.,  -877.,  ...,  -996.,  -941.,  -962.],
          [ -904.,  -960.,  -971.,  ...,  -868.,  -785.,  -968.]],

         [[ -925.,  -933.,  -901.,  ...,  -872.,  -857.,  -931.],
          [ -907.,  -938., -1000.,  ...,  -971.,  -937.,  -921.],
          [ -923.,  -930.,  -871.,  ...,  -882.,  -915.,  -963.],
          ...,
          [ -956.,  -915.,  -986.,  ..., -1000.,  -998.,  -951.],
          [ -874.,  -831.,  -829.,  ...,  -901.,  -887.,  -933.],
          [-1000., -1000.,  -865.,  ..., -1000.,  -973.,  -976.]],

         [[ -948.,  -929.,  -923.,  ...,  -971.,  -942.,  -928.],
          [ -881.,  -892.,  -884.,  ...,  -937.,  -931.,  -911.],
          [ -844.,  -780.,  -851.,  ..., 

(tensor([[[[-840., -884., -902.,  ..., -634., -456., -325.],
          [-852., -887., -924.,  ..., -696., -521., -293.],
          [-855., -892., -923.,  ..., -787., -663., -400.],
          ...,
          [ 876.,  958.,  980.,  ...,  209.,  116.,   76.],
          [ 523.,  588.,  587.,  ...,  201.,  121.,   49.],
          [ 366.,  361.,  292.,  ...,  137.,   68.,   16.]],

         [[-908., -922., -929.,  ..., -712., -498., -383.],
          [-896., -902., -927.,  ..., -746., -628., -471.],
          [-889., -904., -937.,  ..., -786., -752., -608.],
          ...,
          [1000., 1000., 1000.,  ...,   18.,   24.,   43.],
          [ 695.,  704.,  744.,  ...,   34.,   34.,   37.],
          [ 306.,  319.,  336.,  ...,   17.,    5.,    0.]],

         [[-895., -910., -871.,  ..., -889., -870., -825.],
          [-929., -934., -927.,  ..., -902., -905., -857.],
          [-982., -982., -981.,  ..., -915., -914., -866.],
          ...,
          [1000.,  919.,  884.,  ...,   46.,   51.

(tensor([[[[-903., -878., -862.,  ..., -880., -904., -880.],
          [-902., -865., -859.,  ..., -843., -907., -912.],
          [-899., -876., -887.,  ..., -933., -932., -924.],
          ...,
          [-943., -953., -955.,  ...,  -84.,  -40.,    7.],
          [-944., -935., -932.,  ...,  -32.,   -5.,   16.],
          [-935., -913., -918.,  ...,   -6.,   25.,   -9.]],

         [[-933., -934., -939.,  ..., -953., -931., -941.],
          [-919., -930., -925.,  ..., -929., -934., -949.],
          [-923., -922., -932.,  ..., -927., -934., -965.],
          ...,
          [-946., -904., -897.,  ...,  -61.,  -61.,   22.],
          [-933., -912., -913.,  ...,  -57.,  -22.,   22.],
          [-942., -924., -916.,  ...,   -9.,   10.,   23.]],

         [[-953., -955., -939.,  ..., -856., -836., -848.],
          [-960., -958., -939.,  ..., -850., -822., -828.],
          [-945., -941., -940.,  ..., -849., -824., -815.],
          ...,
          [-944., -954., -959.,  ...,  -18.,  -50.

(tensor([[[[ 280.,  280.,  287.,  ..., -917., -847., -788.],
          [ 295.,  290.,  283.,  ..., -925., -862., -809.],
          [ 307.,  306.,  295.,  ..., -911., -845., -804.],
          ...,
          [ 153.,  152.,  162.,  ..., -799., -798., -827.],
          [ 222.,  207.,  192.,  ..., -839., -825., -815.],
          [ 239.,  250.,  220.,  ..., -878., -851., -806.]],

         [[ 232.,  237.,  241.,  ..., -909., -876., -823.],
          [ 259.,  260.,  249.,  ..., -915., -879., -844.],
          [ 286.,  278.,  259.,  ..., -919., -877., -833.],
          ...,
          [ 161.,  167.,  178.,  ..., -645., -712., -816.],
          [ 218.,  221.,  210.,  ..., -681., -754., -825.],
          [ 219.,  215.,  216.,  ..., -778., -819., -837.]],

         [[ 198.,  191.,  178.,  ..., -923., -914., -910.],
          [ 205.,  199.,  183.,  ..., -928., -929., -907.],
          [ 189.,  194.,  189.,  ..., -924., -912., -888.],
          ...,
          [ 134.,  148.,  154.,  ..., -815., -813.

...

(tensor([[[[-924., -933., -949.,  ..., -951., -943., -932.],
          [-929., -924., -921.,  ..., -970., -959., -951.],
          [-940., -926., -922.,  ..., -972., -967., -963.],
          ...,
          [-919., -888., -893.,  ..., -949., -947., -889.],
          [-927., -918., -910.,  ..., -937., -921., -913.],
          [-902., -921., -916.,  ..., -930., -901., -896.]],

         [[-934., -944., -936.,  ..., -921., -940., -964.],
          [-913., -921., -925.,  ..., -960., -952., -946.],
          [-921., -922., -922.,  ..., -975., -971., -946.],
          ...,
          [-888., -905., -940.,  ..., -925., -915., -899.],
          [-879., -889., -915.,  ..., -891., -888., -896.],
          [-912., -904., -897.,  ..., -892., -895., -899.]],

         [[-921., -912., -921.,  ..., -912., -922., -930.],
          [-902., -915., -935.,  ..., -922., -920., -926.],
          [-905., -918., -936.,  ..., -936., -918., -917.],
          ...,
          [-889., -904., -920.,  ..., -936., -911.

(tensor([[[[-727., -797., -825.,  ..., -142.,  -76.,  538.],
          [-792., -888., -866.,  ..., -164.,   69.,  688.],
          [-746., -792., -842.,  ...,  -90.,  323.,  782.],
          ...,
          [-867., -827., -829.,  ..., -104., -183., -149.],
          [-846., -842., -805.,  ...,   62.,  -43., -119.],
          [-742., -782., -761.,  ..., -126.,  -61., -115.]],

         [[-798., -797., -801.,  ..., -126., -122.,  218.],
          [-881., -963., -969.,  ...,  -47.,  -66.,  339.],
          [-840., -731., -801.,  ...,  -56.,   97.,  541.],
          ...,
          [-834., -839., -858.,  ...,  -57., -161., -113.],
          [-860., -818., -741.,  ...,   92.,  -24.,  -92.],
          [-636., -635., -533.,  ..., -121.,  -80.,  -82.]],

         [[-802., -812., -793.,  ..., -163.,  -99.,  -15.],
          [-884., -890., -948.,  ...,  -45.,  -68.,   19.],
          [-905., -775., -860.,  ...,  -64.,  -24.,  185.],
          ...,
          [-822., -848., -864.,  ...,   40.,  -22.

(tensor([[[[-785., -803., -816.,  ..., -824., -808., -808.],
          [-818., -817., -813.,  ..., -834., -817., -823.],
          [-823., -815., -812.,  ..., -850., -851., -859.],
          ...,
          [-825., -827., -825.,  ..., -790., -843., -858.],
          [-852., -829., -797.,  ..., -846., -857., -851.],
          [-869., -840., -754.,  ..., -864., -865., -854.]],

         [[-823., -820., -812.,  ..., -831., -827., -834.],
          [-847., -837., -802.,  ..., -836., -835., -833.],
          [-814., -813., -802.,  ..., -829., -835., -841.],
          ...,
          [-863., -857., -861.,  ..., -792., -839., -860.],
          [-844., -844., -858.,  ..., -838., -836., -843.],
          [-827., -843., -813.,  ..., -862., -842., -833.]],

         [[-769., -737., -697.,  ..., -832., -832., -839.],
          [-912., -841., -757.,  ..., -824., -826., -821.],
          [-893., -858., -845.,  ..., -802., -809., -816.],
          ...,
          [-879., -889., -864.,  ..., -776., -819.

(tensor([[[[-978., -908., -861.,  ...,  253.,  314., -158.],
          [-893., -906., -879.,  ...,  318.,  185., -330.],
          [-815., -863., -904.,  ...,  403.,  170., -579.],
          ...,
          [-851., -833., -913.,  ...,  -16.,    6.,   36.],
          [-938., -948., -969.,  ...,   22.,  -40.,   72.],
          [-959., -860., -919.,  ...,   18.,  -45.,   71.]],

         [[-899., -906., -929.,  ...,  318.,  218., -512.],
          [-911., -936., -924.,  ...,  207.,  182., -438.],
          [-881., -919., -857.,  ...,  135.,  199., -464.],
          ...,
          [-804., -694., -863.,  ...,   49.,   58.,   57.],
          [-876., -680., -892.,  ...,  -38.,    1.,  112.],
          [-945., -777., -909.,  ...,    5.,   32.,   76.]],

         [[-879., -965., -932.,  ...,  353.,   45., -397.],
          [-927., -953., -957.,  ...,  252.,  203.,  -31.],
          [-905., -875., -909.,  ...,  197.,  201.,  155.],
          ...,
          [-914., -913., -913.,  ...,  -70.,    3.

(tensor([[[[  431.,   253.,   -69.,  ...,  -269.,  -151.,  -221.],
          [  -46.,  -176.,  -200.,  ...,   356.,   426.,   478.],
          [   20.,   222.,   450.,  ...,   112.,  -116.,    76.],
          ...,
          [ -310.,  -398.,    89.,  ...,  -142.,   -63.,  -120.],
          [    2.,  -190.,  -213.,  ...,  -583.,  -305.,  -286.],
          [ -290.,  -311.,   128.,  ...,   -83.,   449.,   795.]],

         [[  174.,   -53.,  -162.,  ...,   114.,   108.,  -137.],
          [ -172.,   -84.,     6.,  ...,    54.,   246.,   280.],
          [  106.,   104.,   -82.,  ...,    45.,   -83.,    65.],
          ...,
          [ -405.,  -366.,  -139.,  ...,  -154.,  -129.,  -263.],
          [  199.,   -15.,     0.,  ...,     5.,  -168.,   -26.],
          [ -112.,   -16.,   391.,  ...,   342.,   612.,   358.]],

         [[ -146.,  -113.,  -159.,  ...,   435.,   276.,   241.],
          [ -387.,  -102.,    -1.,  ...,  -279.,   -76.,   -17.],
          [   43.,  -193.,  -198.,  ..., 

In [284]:
lunadataset(dataset)

(tensor([[[[-563., -282.,  -95.,  ...,   33.,   48.,   46.],
          [-445., -195.,  -65.,  ...,   25.,   27.,   26.],
          [-447., -203.,  -59.,  ...,    4.,    8.,   13.],
          ...,
          [ -19., -121., -221.,  ...,   22.,   47.,   58.],
          [ -58., -182., -283.,  ...,   16.,   37.,   49.],
          [-142., -273., -380.,  ...,   25.,   41.,   44.]],

         [[-729., -569., -374.,  ...,   17.,   23.,   27.],
          [-650., -502., -316.,  ...,   20.,   10.,   18.],
          [-663., -483., -249.,  ...,    9.,   -1.,   16.],
          ...,
          [-119., -147., -205.,  ...,   25.,   50.,   69.],
          [ -98., -163., -229.,  ...,   14.,   27.,   47.],
          [-102., -203., -304.,  ...,   18.,   19.,   39.]],

         [[-866., -824., -718.,  ...,   -5.,   -7.,    1.],
          [-829., -792., -653.,  ...,    1.,   -6.,    1.],
          [-806., -736., -517.,  ...,   14.,    3.,    7.],
          ...,
          [-283., -293., -307.,  ...,   54.,   67.

(tensor([[[[  -16.,   -48.,   -56.,  ...,   -35.,    11.,   209.],
          [   94.,    37.,  -100.,  ...,    94.,   140.,   156.],
          [   80.,  -208.,   -44.,  ...,    22.,    73.,     5.],
          ...,
          [  -29.,   -38.,   -68.,  ...,  -386.,  -218.,   -83.],
          [  -51.,  -101.,  -133.,  ...,  -439.,  -127.,  -237.],
          [  -43.,     1.,   -96.,  ...,  -587.,  -478.,  -377.]],

         [[  -86.,  -109.,  -113.,  ...,   105.,   127.,    90.],
          [   87.,     4.,  -127.,  ...,    51.,   -41.,    73.],
          [  -10.,  -202.,   -34.,  ...,   100.,   211.,    94.],
          ...,
          [   66.,   -51.,  -104.,  ...,  -654.,  -571.,  -488.],
          [  -18.,   -97.,  -155.,  ...,  -773.,  -632.,  -789.],
          [  -26.,   -48.,  -199.,  ...,  -777.,  -930.,  -746.]],

         [[  -39.,   -36.,    20.,  ...,   119.,    73.,    45.],
          [   36.,   -65.,  -131.,  ...,   -11.,   -14.,    35.],
          [  -71.,   -53.,     6.,  ..., 

(tensor([[[[ -846.,  -977.,  -976.,  ...,  -780.,  -689.,  -674.],
          [ -884.,  -779.,  -818.,  ...,  -924.,  -958., -1000.],
          [-1000.,  -979.,  -866.,  ..., -1000.,  -830.,  -675.],
          ...,
          [ -875.,  -905.,  -952.,  ...,  -939.,  -796.,  -796.],
          [-1000.,  -936.,  -848.,  ...,  -785.,  -882., -1000.],
          [ -820.,  -780.,  -870.,  ...,  -886.,  -812.,  -837.]],

         [[ -697.,  -730.,  -956.,  ...,  -883.,  -809.,  -851.],
          [ -958.,  -970.,  -830.,  ...,  -964.,  -940., -1000.],
          [ -974.,  -968.,  -984.,  ...,  -900.,  -853.,  -886.],
          ...,
          [-1000., -1000.,  -972.,  ...,  -924.,  -950.,  -814.],
          [-1000.,  -847.,  -880.,  ...,  -724.,  -837.,  -871.],
          [ -889.,  -910.,  -937.,  ..., -1000.,  -984.,  -950.]],

         [[ -838.,  -912.,  -967.,  ..., -1000.,  -917.,  -868.],
          [ -917.,  -879.,  -849.,  ...,  -723.,  -883.,  -992.],
          [ -968.,  -948.,  -913.,  ..., 

(tensor([[[[-784., -876., -881.,  ..., -860., -479., -165.],
          [-810., -790., -817.,  ..., -650., -294.,  -95.],
          [-868., -832., -815.,  ..., -400.,  -15., -135.],
          ...,
          [  69.,  -64.,  -89.,  ..., -159.,   -7.,  -28.],
          [ -54.,  -18.,  -48.,  ...,  162.,  126.,   42.],
          [ 110.,  235.,    0.,  ..., -116., -180.,   24.]],

         [[-705., -847., -836.,  ..., -939., -348., -145.],
          [-772., -902., -843.,  ..., -684., -259.,  -87.],
          [-870., -784., -788.,  ..., -417., -122.,  -77.],
          ...,
          [ -67., -128., -139.,  ...,   29.,  106.,  -17.],
          [  49.,   70.,   68.,  ...,  133.,   28.,  180.],
          [ -53.,   14.,   21.,  ..., -196., -274., -108.]],

         [[-756., -960., -813.,  ..., -875., -544., -240.],
          [-898., -887., -912.,  ..., -740., -373., -126.],
          [-881., -870., -907.,  ..., -437., -229.,   43.],
          ...,
          [  58., -114.,   53.,  ...,  128.,  119.

(tensor([[[[-859., -791., -847.,  ..., -146.,  -99.,   79.],
          [-870., -832., -871.,  ...,  -15., -209.,   -5.],
          [-867., -881., -887.,  ...,  214.,  -76.,  -76.],
          ...,
          [-844., -918., -863.,  ...,   30.,   61.,   18.],
          [-864., -844., -836.,  ...,    7.,   18.,    6.],
          [-946., -899., -830.,  ...,  -31.,   67.,   82.]],

         [[-815., -790., -837.,  ..., -126.,  -82.,   72.],
          [-855., -854., -873.,  ...,   39., -111.,   50.],
          [-929., -886., -872.,  ...,  166.,  -26.,   -1.],
          ...,
          [-883., -935., -884.,  ...,   60.,   69.,   89.],
          [-887., -877., -893.,  ...,   39.,    5.,  109.],
          [-936., -891., -893.,  ...,   -3.,   -7.,   88.]],

         [[-783., -815., -846.,  ...,  -80.,  -98.,  -16.],
          [-846., -873., -872.,  ...,   51.,  -22.,  -38.],
          [-934., -901., -883.,  ...,   54.,   59.,   47.],
          ...,
          [-875., -967., -927.,  ...,   56.,   19.

...

(tensor([[[[-782., -761., -731.,  ..., -538., -731., -809.],
          [-740., -746., -759.,  ..., -138., -286., -399.],
          [-716., -693., -673.,  ...,   16.,    6.,  -20.],
          ...,
          [-818., -841., -845.,  ...,  -16.,  167.,  317.],
          [-759., -798., -816.,  ...,   46.,  288.,  364.],
          [-798., -819., -828.,  ...,  109.,  394.,  418.]],

         [[-787., -625., -548.,  ..., -342., -621., -780.],
          [-798., -700., -709.,  ...,  -67., -225., -353.],
          [-811., -805., -748.,  ...,   15.,    4.,   -9.],
          ...,
          [-812., -843., -856.,  ...,  103.,  169.,  366.],
          [-828., -886., -922.,  ...,  135.,  250.,  439.],
          [-804., -842., -895.,  ...,  125.,  343.,  427.]],

         [[-367., -123.,  -45.,  ...,  -84., -414., -753.],
          [-563., -350., -302.,  ...,   46.,   -1., -219.],
          [-771., -656., -534.,  ...,   15.,   76.,   68.],
          ...,
          [-865., -858., -852.,  ...,   78.,   86.

(tensor([[[[-454., -411., -476.,  ..., -690., -776., -774.],
          [-476., -376., -259.,  ..., -575., -652., -690.],
          [-414., -409., -203.,  ..., -545., -585., -662.],
          ...,
          [-807., -755., -680.,  ...,  -35.,   70.,  538.],
          [-717., -689., -574.,  ...,   21.,  250.,  700.],
          [-680., -581., -371.,  ...,    0.,  336.,  800.]],

         [[-610., -480., -381.,  ..., -626., -725., -756.],
          [-627., -514., -422.,  ..., -663., -742., -765.],
          [-649., -525., -486.,  ..., -656., -749., -748.],
          ...,
          [-777., -717., -551.,  ...,    1.,  282.,  850.],
          [-730., -619., -382.,  ...,   22.,  502.,  983.],
          [-748., -589., -324.,  ...,  116.,  734., 1000.]],

         [[-683., -702., -735.,  ..., -690., -714., -774.],
          [-638., -653., -660.,  ..., -730., -755., -797.],
          [-727., -719., -727.,  ..., -701., -725., -777.],
          ...,
          [-833., -807., -742.,  ...,  -70.,  234.

(tensor([[[[ -173.,    71.,    71.,  ...,    -9.,  -452.,   337.],
          [ -112.,  -156.,   166.,  ...,    -8.,    39.,   -77.],
          [   49.,   -31.,  -611.,  ...,    16.,    92.,  -116.],
          ...,
          [ -265.,  -430.,  -933.,  ..., -1000.,  -865., -1000.],
          [ -724.,  -625.,  -257.,  ...,  -561., -1000.,  -803.],
          [ -874.,  -622.,  -884.,  ..., -1000.,  -464.,  -906.]],

         [[ -396.,   -20.,   167.,  ...,  -297.,  -148.,   607.],
          [  305.,  -281.,   -69.,  ...,   519.,     1.,  -236.],
          [ -230.,    87.,  -364.,  ...,  -363.,   -40.,   439.],
          ...,
          [ -559.,  -732.,  -751.,  ...,  -976.,  -387., -1000.],
          [ -816.,  -494.,  -839.,  ...,  -691., -1000.,  -572.],
          [ -549., -1000.,  -657.,  ..., -1000.,  -503.,  -907.]],

         [[ -138.,   -52.,   287.,  ...,    18.,    10.,    -6.],
          [   -5.,  -157.,  -255.,  ...,    74.,   474.,  -230.],
          [  -47.,    -3.,  -428.,  ..., 

(tensor([[[[ -775.,  -799.,  -874.,  ...,  -965.,  -995.,  -993.],
          [ -855.,  -778.,  -779.,  ...,  -929.,  -972., -1000.],
          [ -782.,  -830.,  -847.,  ...,  -643.,  -223.,   -91.],
          ...,
          [ -381.,  -828.,  -826.,  ...,  -710.,  -647.,  -699.],
          [ -407.,  -816.,  -836.,  ...,  -839.,  -803.,  -867.],
          [ -781.,  -852.,  -795.,  ...,  -730.,  -841.,  -840.]],

         [[ -657.,  -898.,  -852.,  ...,  -908.,  -947.,  -975.],
          [ -739.,  -872.,  -827.,  ...,  -909.,  -929.,  -911.],
          [ -758.,  -832.,  -835.,  ..., -1000.,  -552.,    79.],
          ...,
          [ -571.,  -804.,  -826.,  ...,  -483.,  -567.,  -747.],
          [ -716.,  -811.,  -904.,  ...,  -501.,  -476.,  -442.],
          [ -875.,  -791.,  -811.,  ...,  -929.,  -903.,  -832.]],

         [[ -250.,  -823.,  -784.,  ...,  -909., -1000., -1000.],
          [ -490.,  -816.,  -777.,  ...,  -907.,  -977.,  -899.],
          [ -648.,  -862.,  -857.,  ..., 

(tensor([[[[ -925.,  -934.,  -909.,  ...,  -395.,   -82.,    92.],
          [ -904.,  -924.,  -895.,  ...,  -755.,  -591.,  -264.],
          [ -880.,  -907.,  -908.,  ...,  -854.,  -867.,  -748.],
          ...,
          [ -812.,  -764.,  -791.,  ...,  -776.,  -737.,  -751.],
          [ -772.,  -753.,  -784.,  ...,  -812.,  -773.,  -759.],
          [ -714.,  -762.,  -765.,  ...,  -830.,  -800.,  -777.]],

         [[ -938.,  -932.,  -908.,  ...,  -305.,  -145.,   -15.],
          [ -941.,  -935.,  -905.,  ...,  -384.,  -283.,  -126.],
          [ -930.,  -944.,  -932.,  ...,  -558.,  -435.,  -311.],
          ...,
          [ -916.,  -926.,  -914.,  ...,  -823.,  -586.,  -275.],
          [ -923.,  -932.,  -940.,  ...,  -882.,  -793.,  -517.],
          [ -886.,  -935.,  -968.,  ...,  -898.,  -847.,  -703.]],

         [[ -932.,  -912.,  -914.,  ...,  -759.,  -636.,  -376.],
          [ -961.,  -943.,  -927.,  ...,  -837.,  -752.,  -609.],
          [ -982.,  -987.,  -958.,  ..., 

In [274]:
print(time.time())

1662104653.148999
